# {class}`~tvm.contrib.msc.pipeline.MSCManager`

In [1]:
%cd ..
from pathlib import Path

temp_dir = Path(".temp")
temp_dir.mkdir(exist_ok=True)

/media/pc/data/lxw/ai/tvm-book/doc/tutorials/msc


In [2]:
def _get_torch_model(name, training=False):
    """Get model from torch vision"""

    # pylint: disable=import-outside-toplevel
    try:
        import torchvision

        model = getattr(torchvision.models, name)()
        if training:
            model = model.train()
        else:
            model = model.eval()
        return model
    except:  # pylint: disable=bare-except
        print("please install torchvision package")
        return None

In [3]:
from tvm.contrib.msc.core import utils as msc_utils

def _get_config(model_type, compile_type, inputs, outputs, dynamic=False, atol=1e-1, rtol=1e-1):
    """Get msc config"""

    path = f'test_pipe_{model_type}_{compile_type}_{"dynamic" if dynamic else "static"}'
    return {
        "workspace": msc_utils.msc_dir(f"{temp_dir}/{path}", keep_history=False),
        "verbose": "critical",
        "model_type": model_type,
        "inputs": inputs,
        "outputs": outputs,
        "dataset": {"prepare": {"loader": "from_random", "max_iter": 5}},
        "prepare": {"profile": {"benchmark": {"repeat": 10}}},
        "baseline": {
            "run_type": model_type,
            "profile": {"check": {"atol": atol, "rtol": rtol}, "benchmark": {"repeat": 10}},
        },
        "compile": {
            "run_type": compile_type,
            "profile": {"check": {"atol": atol, "rtol": rtol}, "benchmark": {"repeat": 10}},
        },
    }

In [4]:
from tvm.contrib.msc.pipeline import MSCManager
from tvm.contrib.msc.core.utils.namespace import MSCFramework
import torch

for compile_type in [MSCFramework.TORCH, MSCFramework.TVM]:
    torch_model = _get_torch_model("resnet50", False)
    if torch.cuda.is_available():
        torch_model = torch_model.to(torch.device("cuda:0"))
    config = _get_config(
        MSCFramework.TORCH,
        compile_type,
        inputs=[["input_0", [1, 3, 224, 224], "float32"]],
        outputs=["output"],
        dynamic = True,
        atol = 1e-1,
        rtol = 1e-1,
    )
    pipeline = MSCManager(torch_model, config)
    pipeline.run_pipe() # 运行管道
    print(pipeline.get_runtime().model_info) # 打印模型信息
    pipeline.destory() # 销毁管道

/media/pc/data/lxw/ai/tvm/python/tvm/contrib/msc/framework/torch/codegen/codegen.py:74: FutureWarning: You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be loaded via this mode unless they are explicitly allowlisted by the user via `torch.serialization.add_safe_globals`. We recommend you start setting `weights_only=True` for any use case where you don't have full control of the loaded file. Please open an issue on GitHub for any issues related to this experimental feature.
  state_dict = torch.load(folder.relpath(

{'inputs': [{'name': 'input_0', 'shape': [1, 3, 224, 224], 'dtype': 'float32', 'layout': 'NCHW'}], 'outputs': [{'name': 'output', 'shape': [1, 1000], 'dtype': 'float32', 'layout': 'NW'}], 'nodes': {'total': 229, 'input': 1, 'nn.conv2d': 53, 'nn.batch_norm': 53, 'get_item': 53, 'nn.relu': 49, 'nn.max_pool2d': 1, 'add': 16, 'nn.adaptive_avg_pool2d': 1, 'reshape': 1, 'msc.linear_bias': 1}}


/media/pc/data/lxw/ai/tvm/python/tvm/contrib/msc/framework/torch/codegen/codegen.py:74: FutureWarning: You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be loaded via this mode unless they are explicitly allowlisted by the user via `torch.serialization.add_safe_globals`. We recommend you start setting `weights_only=True` for any use case where you don't have full control of the loaded file. Please open an issue on GitHub for any issues related to this experimental feature.
  state_dict = torch.load(folder.relpath(

{'inputs': [{'name': 'input_0', 'shape': [1, 3, 224, 224], 'dtype': 'float32', 'layout': 'NCHW'}], 'outputs': [{'name': 'output', 'shape': [1, 1000], 'dtype': 'float32', 'layout': 'NW'}], 'nodes': {'total': 229, 'input': 1, 'nn.conv2d': 53, 'nn.batch_norm': 53, 'get_item': 53, 'nn.relu': 49, 'nn.max_pool2d': 1, 'add': 16, 'nn.adaptive_avg_pool2d': 1, 'reshape': 1, 'msc.linear_bias': 1}}
